# Pythagorean Expectation Via Weibull Distribution

The goal of this notebook is to build a model to predict the winner of a baseball game using the data gathered as a season goes forward. The main idea of rather using the Pythagorean Expectation is to use the idea of Steven J. Miller's paper "A Derivation of the Pythagorean Won-Lose Formula in Baseball" (see https://arxiv.org/pdf/math/0509698.pdf). However, rather using the actual Pythagorean Expectation as our measure of whether or not a team will win, we will use the empirical observation that the Pythagorean Expectation is a good approximation for the actual win percentage in baseball. Furthermore, as the paper shows the Pythagorean Expectation gives the precise win percentage when we make the assumption that the runs scored and runs allowed follow Weibull distributions with given parameters. Thus, the idea of the model will be to use this observation, so for any particular game between two games look at how the teams previously did throughout the season to determine what the appropriate parameters for their Weibull distribution will be for that particular game. Then we shall simulate several games for how many runs will be scored by each team using these distributions to predict who will win the game. 

Note: this notebook is meant more of a proof of concept, so we shall only focus on the data from the 2010 season. 

In [1]:
##Import of packages that we will use 
import pandas as pd
import numpy as np
import math

Note: the data we are reading in will be an adjusted version of Joe's game data, but we have removed the variables which we do not use (i.e. win percentage, pythagorean expectation, etc.), we have also added additional columns that we will be using to get the parameters for the Weibull distribution. Primarily, we have added a cumulative runs scored and allowed columns which consist of the cumulative runs scored and allowed before that particular game (thus for the first game each team will have 0 to initialize). We have used these cumulative runs/scored and allowed to calculate the Weibull distribution parameters at that point in the season.

Remark: The three parameter Weibull distribution has pdf 
$$
f(x;\alpha,\beta,\gamma)=\begin{cases}
\frac{\gamma}{\alpha}\left(\frac{x-\beta}{\alpha}\right)^{\gamma-1}e^{-\left(\frac{x-\beta}{\alpha}\right)^\gamma} & x\geq \beta\\
0 & \text{else}
\end{cases}
$$
Per the paper, we note that $\gamma$ corresponds to the exponent appearing in the Pythagorean Expectation formula, for simplicity of the model, we shall make the assumption in what follows is that $\gamma=1.82$ as a constant which we shall not change. Furthermore, per the commment the variable $\beta$ is just a translation which has no affect if we assume that it is constant in all cases (and was included, so that the ideas may be extrapolated to other sports with higher scoring games). For baseball Miller takes $\beta=-.5$, so that the bins are centered at integers. Thus, we shall take these variables to be constant throughout. Now per equation (2.8), we have a formula for the parameter $\alpha$ for each team given by 
$$
\alpha_{RS}(n+1)=\frac{RS(n)-\beta}{\Gamma(1+\gamma^{-1})}
$$
and
$$
\alpha_{RA}=\frac{RA-\beta}{\Gamma(1+\gamma^{-1})}
$$
Thus, if we use the previous RS and RA for a team, we can assume that their RS and RA follow a Weibull distirbution with the above parameters. Then there will be two ways that we can predict how each team will win (namely using the RS or RA for each team). 

In [2]:
#Initialize our values of gamma and beta as
#we are fixing them now, but might play with
#this later
gamma = 1.82
beta = 0

In [3]:
##Read data from Joe's csv file as gl_2010 (i.e. game log 2010)
gl_2010 = pd.read_csv("./sorted_game_logs/smaller_2010.csv")

In [1]:
##We can take a quick look at our data
gl_2010.head()

NameError: name 'gl_2010' is not defined

In [5]:
#Gives the list of teams and alphabetizes it
team_list = gl_2010.team.value_counts().keys()
team_list = sorted(team_list)

We will now make the data that we need, but we shall do this individually for ANA as a test case, and then we will generalize it for all the other teams all at once 

In [6]:
#This is a function that takes in a dataframe
#for an individual team, and returns a series
#which gives the cumulative sum of the runs scored
#for all the games prior to that given one
def make_previous_cum_sum_rs(df):
    cumsumlist = [0]
    for x in df.runs_scored.cumsum():
        cumsumlist.append(x)
    cumsumlist.pop()
    return pd.Series(cumsumlist)
#This is an analogous function for runs allowed
def make_previous_cum_sum_ra(df):
    cumsumlist = [0]
    for x in df.runs_allowed.cumsum():
        cumsumlist.append(x)
    cumsumlist.pop()
    return pd.Series(cumsumlist)    

In [7]:
#This is a function that takes in the data frame
#it then takes the given cumulative runs scored
#from all previous games, and uses it to construct
#
def make_alpha_rs(df, beta, gamma):
    return (df.previous_cumulative_runs_scored - beta) / (math.gamma(1 + (1 / gamma)))
#This is the analogous function for runs allowed
def make_alpha_ra(df, beta, gamma):
    return (df.previous_cumulative_runs_allowed - beta) / (math.gamma(1 + (1 / gamma)))

In [8]:
#Creates a dataframe just for the team ANA
ANA_2010 = gl_2010.loc[gl_2010.team == "ANA"]
ANA_2010.head()

Date team opponent  runs_scored  runs_allowed  game_number  win_loss
0  20100405  ANA      MIN            6             3            1         1
1  20100406  ANA      MIN            3             5            2         0
2  20100407  ANA      MIN            2             4            3         0
3  20100408  ANA      MIN            1            10            4         0
4  20100409  ANA      OAK            4            10            5         0

In [9]:
#We shall add columns for cumulative RS, RA, 
#and the corresponding Weibull pararmeters
ANA_2010.insert(7,"previous_cumulative_runs_scored", make_previous_cum_sum_rs(ANA_2010))
ANA_2010.insert(8,"previous_cumulative_runs_allowed", make_previous_cum_sum_ra(ANA_2010))
ANA_2010.insert(9,"alpha_rs", make_alpha_rs(ANA_2010, beta, gamma))
ANA_2010.insert(10,"alpha_ra", make_alpha_ra(ANA_2010, beta, gamma))

In [10]:
ANA_2010.head()

Date team opponent  runs_scored  runs_allowed  game_number  win_loss  \
0  20100405  ANA      MIN            6             3            1         1   
1  20100406  ANA      MIN            3             5            2         0   
2  20100407  ANA      MIN            2             4            3         0   
3  20100408  ANA      MIN            1            10            4         0   
4  20100409  ANA      OAK            4            10            5         0   

   previous_cumulative_runs_scored  previous_cumulative_runs_allowed  \
0                                0                                 0   
1                                6                                 3   
2                                9                                 8   
3                               11                                12   
4                               12                                22   

    alpha_rs   alpha_ra  
0   0.000000   0.000000  
1   6.750460   3.375230  
2  10.125690   9.000613  
3  12.375843  13.500920  
4  13.500920  24.751687

We will now break everything up in terms of the teams for the general case of the code to break things into each of the teams

In [11]:
#This function takes in our data and the name of the team and 
#returns a dataframe that is just for that specific team
#it then calls a function that adds the additional data we 
#want from what we have
def make_df_for_team(gamelog, team):
    df = gamelog.loc[gamelog.team == team].reset_index() 
    #Note we had to reindex otherwise only the first 
    return make_df_from_team_df(df)
    
#This function takes in the dataframe for a specific team
#It then appends new columns with the additional data that we 
#are interested in which we will be using
def make_df_from_team_df(df):
    df.insert(8,"previous_cumulative_runs_scored", make_previous_cum_sum_rs(df))
    df.insert(9,"previous_cumulative_runs_allowed", make_previous_cum_sum_ra(df))
    df.insert(10,"alpha_rs", make_alpha_rs(df, beta, gamma))
    df.insert(11,"alpha_ra", make_alpha_ra(df, beta, gamma))
    return df

In [12]:
#Make a list for the data frame for each team
frames = []
for team in team_list:
    df = make_df_for_team(gl_2010, team)#for each data frame we get the rest of the data we want
    frames.append(df)  #adds the dataframe for that team to the list
result = pd.concat(frames) #puts together all the dataframes into a single dataframe
result["alpha_rs"] = result["alpha_rs"] + (result["alpha_rs"] == 0) #adds 1 if alpha_rs = 0
result["alpha_ra"] = result["alpha_ra"] + (result["alpha_ra"] == 0) #adds 1 if alpha_ra = 0

In [13]:
result

index      Date team opponent  runs_scored  runs_allowed  game_number  \
0        0  20100405  ANA      MIN            6             3            1   
1        1  20100406  ANA      MIN            3             5            2   
2        2  20100407  ANA      MIN            2             4            3   
3        3  20100408  ANA      MIN            1            10            4   
4        4  20100409  ANA      OAK            4            10            5   
..     ...       ...  ...      ...          ...           ...          ...   
157   4855  20100928  WAS      PHI            2             1          158   
158   4856  20100929  WAS      PHI            1             7          159   
159   4857  20101001  WAS      NYN            1             2          160   
160   4858  20101002  WAS      NYN            2             7          161   
161   4859  20101003  WAS      NYN            2             1          162   

     win_loss  previous_cumulative_runs_scored  \
0           1                                0   
1           0                                6   
2           0                                9   
3           0                               11   
4           0                               12   
..        ...                              ...   
157         1                              647   
158         0                              649   
159         0                              650   
160         0                              651   
161         1                              653   

     previous_cumulative_runs_allowed    alpha_rs    alpha_ra  
0                                   0    1.000000    1.000000  
1                                   3    6.750460    3.375230  
2                                   8   10.125690    9.000613  
3                                  12   12.375843   13.500920  
4                                  22   13.500920   24.751687  
..                                ...         ...         ...  
157                               724  727.924607  814.555511  
158                               725  730.174761  815.680588  
159                               732  731.299837  823.556124  
160                               734  732.424914  825.806278  
161                               741  734.675067  833.681814  

[4860 rows x 12 columns]

Now that we have the data that we are interested in, we can now build up our predictive model, we shall do this by using the alpha_ra and alpha_rs variables as our variables for our Weibull distributions for each team.

We shall now go through things for the first game of the season before writing the code that will do it all at once. Note that this code only works for the first game of the season, but when iterated, we found that it failed at game 4 because CHA's game 4 was against MIN and ANA also was against MIN in game 4, so we have to go about this a separate way. 

In [14]:
#Just get the games for the first game
games = result.loc[result.game_number == 4].reset_index()

In [15]:
games

level_0  index      Date team opponent  runs_scored  runs_allowed  \
0         3      3  20100408  ANA      MIN            1            10   
1         3    165  20100409  ARI      PIT            9             1   
2         3    327  20100409  ATL      SFN            4             5   
3         3    489  20100409  BAL      TOR            6             7   
4         3    651  20100409  BOS      KCA            3             4   
5         3    813  20100409  CHA      MIN            3             4   
6         3    975  20100409  CHN      CIN            4             5   
7         3   1137  20100409  CIN      CHN            5             4   
8         3   1299  20100409  CLE      DET            2             5   
9         3   1461  20100409  COL      SDN            7             0   
10        3   1623  20100409  DET      CLE            5             2   
11        3   1785  20100409  FLO      LAN            3             7   
12        3   1947  20100409  HOU      PHI            0             8   
13        3   2109  20100409  KCA      BOS            4             3   
14        3   2271  20100409  LAN      FLO            7             3   
15        3   2433  20100409  MIL      SLN            4             5   
16        3   2595  20100408  MIN      ANA           10             1   
17        3   2757  20100409  NYA      TBA            3             9   
18        3   2919  20100409  NYN      WAS            8             2   
19        3   3081  20100408  OAK      SEA            6             2   
20        3   3243  20100409  PHI      HOU            8             0   
21        3   3405  20100409  PIT      ARI            1             9   
22        3   3567  20100409  SDN      COL            0             7   
23        3   3729  20100408  SEA      OAK            2             6   
24        3   3891  20100409  SFN      ATL            5             4   
25        3   4053  20100409  SLN      MIL            5             4   
26        3   4215  20100409  TBA      NYA            9             3   
27        3   4377  20100409  TEX      SEA            6             2   
28        3   4539  20100409  TOR      BAL            7             6   
29        3   4701  20100409  WAS      NYN            2             8   

    game_number  win_loss  previous_cumulative_runs_scored  \
0             4         0                               11   
1             4         1                               14   
2             4         0                               19   
3             4         0                               11   
4             4         0                               14   
5             4         0                               12   
6             4         0                                9   
7             4         1                               11   
8             4         0                               10   
9             4         1                               14   
10            4         1                               17   
11            4         0                               11   
12            4         0                                6   
13            4         1                               10   
14            4         1                               18   
15            4         0                               15   
16            4         1                               12   
17            4         0                               16   
18            4         1                               14   
19            4         1                               11   
20            4         1                               24   
21            4         0                               17   
22            4         0                               12   
23            4         0                               11   
24            4         1                               18   
25            4         1                               18   
26            4         1                               12   
27  

In [16]:
#Now we can check the games we get
len(games.T)

13

In [17]:
def run_simulation_same_rs (alpha1_rs, alpha2_rs):
    team1wincount = 0
    for x in range(1001):
        rs1 = gamma * np.random.weibull(alpha1_rs)
        rs2 = gamma * np.random.weibull(alpha2_rs)
        if (rs1>rs2):
            team1wincount = team1wincount + 1
    return team1wincount

def run_simulation_same_ra (alpha1_ra, alpha2_ra):
    team1wincount = 0
    for x in range(1001):
        ra1 = gamma * np.random.weibull(alpha1_ra)
        ra2 = gamma * np.random.weibull(alpha2_ra)
        if (ra2>ra1):
            team1wincount = team1wincount + 1
    return team1wincount

def run_simulation_rs_ra (alpha1_rs, alpha1_ra, alpha2_rs,alpha2_ra):
    team1wincount = 0
    for x in range(1001):
        rs1 = gamma * np.random.weibull(alpha1_rs)
        rs2 = gamma * np.random.weibull(alpha2_rs)
        ra1 = gamma * np.random.weibull(alpha1_ra)
        ra2 = gamma * np.random.weibull(alpha2_ra)
        if (rs1-ra2>rs2-ra1):
            team1wincount = team1wincount + 1
    return team1wincount

In [18]:
#Makes an empty list of all the teams that will be played
teams_played = []
games = result.loc[result.game_number == 4].reset_index()
#Creates a for loop that goes through each of the rows for 
#the particular game we are interested in
games.insert(len(games.T),"same_rs_percentage",0)
games.insert(len(games.T),"same_ra_percentage",0)
games.insert(len(games.T),"both_percentage",0)
for game in range(games.shape[0]):
    #For the particular game we are interested in we now
    #look at all the teams in the roster
    for team in team_list:
        #If the team that we are interested in has not
        #played yet, then we add it and its opponent to 
        #the teams played list, and simulate the games 
        #of it with its opponent
        if games.team[game] not in teams_played:
            if games.opponent[game] not in teams_played:
                teams_played.append(games.opponent[game])
            if games.team[game] not in teams_played:
                teams_played.append(games.team[game])
            print(games.loc[games.opponent == games.team[game]].index)
            opponents_index = games.loc[games.opponent == games.team[game]].index[0]
            team1wincount_same_rs = run_simulation_same_rs(games.alpha_rs[game]
                                                           ,games.alpha_rs[opponents_index])
            team1wincount_same_ra = run_simulation_same_ra(games.alpha_ra[game]
                                                           ,games.alpha_ra[opponents_index])
            team1wincount_different = run_simulation_rs_ra (games.alpha_rs[game], 
                                                            games.alpha_ra[game], 
                                                            games.alpha_rs[opponents_index],
                                                            games.alpha_ra[opponents_index])
            print(team1wincount_same_rs)
            games["same_rs_percentage"][game] = team1wincount_same_rs/101
            games["same_rs_percentage"][opponents_index] = 1 - team1wincount_same_rs/101
            games["same_ra_percentage"][game] = team1wincount_same_ra/101
            games["same_ra_percentage"][opponents_index] = 1 - team1wincount_same_ra/101
            games["both_percentage"][game] = team1wincount_different/101
            games["both_percentage"][opponents_index] = 1 - team1wincount_different/101

Int64Index([16], dtype='int64')
481
Int64Index([21], dtype='int64')
487
Int64Index([24], dtype='int64')
508
Int64Index([28], dtype='int64')
503
Int64Index([13], dtype='int64')
514
Int64Index([], dtype='int64')


C:\Users\steve\AppData\Local\Temp\ipykernel_13508\6021724.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  games["same_rs_percentage"][game] = team1wincount_same_rs/101
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\6021724.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  games["same_ra_percentage"][game] = team1wincount_same_ra/101
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\6021724.py:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-vie

IndexError: index 0 is out of bounds for axis 0 with size 0

In [19]:
games

level_0  index      Date team opponent  runs_scored  runs_allowed  \
0         3      3  20100408  ANA      MIN            1            10   
1         3    165  20100409  ARI      PIT            9             1   
2         3    327  20100409  ATL      SFN            4             5   
3         3    489  20100409  BAL      TOR            6             7   
4         3    651  20100409  BOS      KCA            3             4   
5         3    813  20100409  CHA      MIN            3             4   
6         3    975  20100409  CHN      CIN            4             5   
7         3   1137  20100409  CIN      CHN            5             4   
8         3   1299  20100409  CLE      DET            2             5   
9         3   1461  20100409  COL      SDN            7             0   
10        3   1623  20100409  DET      CLE            5             2   
11        3   1785  20100409  FLO      LAN            3             7   
12        3   1947  20100409  HOU      PHI            0             8   
13        3   2109  20100409  KCA      BOS            4             3   
14        3   2271  20100409  LAN      FLO            7             3   
15        3   2433  20100409  MIL      SLN            4             5   
16        3   2595  20100408  MIN      ANA           10             1   
17        3   2757  20100409  NYA      TBA            3             9   
18        3   2919  20100409  NYN      WAS            8             2   
19        3   3081  20100408  OAK      SEA            6             2   
20        3   3243  20100409  PHI      HOU            8             0   
21        3   3405  20100409  PIT      ARI            1             9   
22        3   3567  20100409  SDN      COL            0             7   
23        3   3729  20100408  SEA      OAK            2             6   
24        3   3891  20100409  SFN      ATL            5             4   
25        3   4053  20100409  SLN      MIL            5             4   
26        3   4215  20100409  TBA      NYA            9             3   
27        3   4377  20100409  TEX      SEA            6             2   
28        3   4539  20100409  TOR      BAL            7             6   
29        3   4701  20100409  WAS      NYN            2             8   

    game_number  win_loss  previous_cumulative_runs_scored  \
0             4         0                               11   
1             4         1                               14   
2             4         0                               19   
3             4         0                               11   
4             4         0                               14   
5             4         0                               12   
6             4         0                                9   
7             4         1                               11   
8             4         0                               10   
9             4         1                               14   
10            4         1                               17   
11            4         0                               11   
12            4         0                                6   
13            4         1                               10   
14            4         1                               18   
15            4         0                               15   
16            4         1                               12   
17            4         0                               16   
18            4         1                               14   
19            4         1                               11   
20            4         1                               24   
21            4         0                               17   
22            4         0                               12   
23            4         0                               11   
24            4         1                               18   
25            4         1                               18   
26            4         1                               12   
27  

In [20]:
games.insert(len(games.T),"same_rs_prediction",(games["same_rs_percentage"].values>.5)*1)
games.insert(len(games.T),"same_ra_prediction",(games["same_ra_percentage"].values>.5)*1)
games.insert(len(games.T),"both_prediction",(games["both_percentage"].values>.5)*1)

In [21]:
games

level_0  index      Date team opponent  runs_scored  runs_allowed  \
0         3      3  20100408  ANA      MIN            1            10   
1         3    165  20100409  ARI      PIT            9             1   
2         3    327  20100409  ATL      SFN            4             5   
3         3    489  20100409  BAL      TOR            6             7   
4         3    651  20100409  BOS      KCA            3             4   
5         3    813  20100409  CHA      MIN            3             4   
6         3    975  20100409  CHN      CIN            4             5   
7         3   1137  20100409  CIN      CHN            5             4   
8         3   1299  20100409  CLE      DET            2             5   
9         3   1461  20100409  COL      SDN            7             0   
10        3   1623  20100409  DET      CLE            5             2   
11        3   1785  20100409  FLO      LAN            3             7   
12        3   1947  20100409  HOU      PHI            0             8   
13        3   2109  20100409  KCA      BOS            4             3   
14        3   2271  20100409  LAN      FLO            7             3   
15        3   2433  20100409  MIL      SLN            4             5   
16        3   2595  20100408  MIN      ANA           10             1   
17        3   2757  20100409  NYA      TBA            3             9   
18        3   2919  20100409  NYN      WAS            8             2   
19        3   3081  20100408  OAK      SEA            6             2   
20        3   3243  20100409  PHI      HOU            8             0   
21        3   3405  20100409  PIT      ARI            1             9   
22        3   3567  20100409  SDN      COL            0             7   
23        3   3729  20100408  SEA      OAK            2             6   
24        3   3891  20100409  SFN      ATL            5             4   
25        3   4053  20100409  SLN      MIL            5             4   
26        3   4215  20100409  TBA      NYA            9             3   
27        3   4377  20100409  TEX      SEA            6             2   
28        3   4539  20100409  TOR      BAL            7             6   
29        3   4701  20100409  WAS      NYN            2             8   

    game_number  win_loss  previous_cumulative_runs_scored  \
0             4         0                               11   
1             4         1                               14   
2             4         0                               19   
3             4         0                               11   
4             4         0                               14   
5             4         0                               12   
6             4         0                                9   
7             4         1                               11   
8             4         0                               10   
9             4         1                               14   
10            4         1                               17   
11            4         0                               11   
12            4         0                                6   
13            4         1                               10   
14            4         1                               18   
15            4         0                               15   
16            4         1                               12   
17            4         0                               16   
18            4         1                               14   
19            4         1                               11   
20            4         1                               24   
21            4         0                               17   
22            4         0                               12   
23            4         0                               11   
24            4         1                               18   
25            4         1                               18   
26            4         1                               12   
27  

In [22]:
games["same_rs_percentage"].values>.5

array([ True,  True,  True,  True,  True, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False])

In [23]:
def simulate_game(result, game_number, team_list):
    games = result.loc[result.game_number == game_number].reset_index()
    #Makes an empty list of all the teams that will be played
    teams_played = []
    #Creates a for loop that goes through each of the rows for 
    #the particular game we are interested in
    games.insert(len(games.T),"same_rs_percentage",0)
    games.insert(len(games.T),"same_ra_percentage",0)
    games.insert(len(games.T),"both_percentage",0)
    for game in range(games.shape[0]):
        #For the particular game we are interested in we now
        #look at all the teams in the roster
        for team in team_list:
            #If the team that we are interested in has not
            #played yet, then we add it and its opponent to 
            #the teams played list, and simulate the games 
            #of it with its opponent
            if games.team[game] not in teams_played:
                if games.opponent[game] not in teams_played:
                    teams_played.append(games.opponent[game])
                if games.team[game] not in teams_played:
                    teams_played.append(games.team[game])
                opponents_index = games.loc[games.opponent == games.team[game]].index[0]
                team1wincount_same_rs = run_simulation_same_rs(games.alpha_rs[game]
                                                           ,games.alpha_rs[opponents_index])
                team1wincount_same_ra = run_simulation_same_ra(games.alpha_ra[game]
                                                           ,games.alpha_ra[opponents_index])
                team1wincount_different = run_simulation_rs_ra (games.alpha_rs[game], 
                                                            games.alpha_ra[game], 
                                                            games.alpha_rs[opponents_index],
                                                            games.alpha_ra[opponents_index])
                #print(team1wincount_same_rs)
                games["same_rs_percentage"][game] = team1wincount_same_rs/101
                games["same_rs_percentage"][opponents_index] = 1 - team1wincount_same_rs/101
                games["same_ra_percentage"][game] = team1wincount_same_ra/101
                games["same_ra_percentage"][opponents_index] = 1 - team1wincount_same_ra/101
                games["both_percentage"][game] = team1wincount_different/101
                games["both_percentage"][opponents_index] = 1 - team1wincount_different/101
    return games

In [33]:
#This will loop through going through each game 
#number of the season
#Make a list for the data frame for each team
frames = []
for game_number in range(3):
    print(game_number)
    df = simulate_game(result,game_number + 1 , team_list) #for each data frame we get the rest of the data we want
    frames.append(df)  #adds the dataframe for that team to the list
final_results = pd.concat(frames)
        
    

0
1


C:\Users\steve\AppData\Local\Temp\ipykernel_13508\69801076.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  games["same_rs_percentage"][game] = team1wincount_same_rs/101
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\69801076.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  games["same_ra_percentage"][game] = team1wincount_same_ra/101
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\69801076.py:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-

2


C:\Users\steve\AppData\Local\Temp\ipykernel_13508\69801076.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  games["same_rs_percentage"][game] = team1wincount_same_rs/101
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\69801076.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  games["same_ra_percentage"][game] = team1wincount_same_ra/101
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\69801076.py:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-

In [34]:
final_results

level_0  index      Date team opponent  runs_scored  runs_allowed  \
0         0      0  20100405  ANA      MIN            6             3   
1         0    162  20100405  ARI      SDN            6             3   
2         0    324  20100405  ATL      CHN           16             5   
3         0    486  20100406  BAL      TBA            3             4   
4         0    648  20100404  BOS      NYA            9             7   
..      ...    ...       ...  ...      ...          ...           ...   
25        2   4052  20100408  SLN      CIN            1             2   
26        2   4214  20100408  TBA      BAL            4             5   
27        2   4376  20100408  TEX      TOR            1             3   
28        2   4538  20100408  TOR      TEX            3             1   
29        2   4700  20100408  WAS      PHI            6             5   

    game_number  win_loss  previous_cumulative_runs_scored  \
0             1         1                                0   
1             1         1                                0   
2             1         1                                0   
3             1         0                                0   
4             1         1                                0   
..          ...       ...                              ...   
25            3         0                               17   
26            3         0                                8   
27            3         0                                9   
28            3         1                               11   
29            3         1                                5   

    previous_cumulative_runs_allowed   alpha_rs   alpha_ra  \
0                                  0   1.000000   1.000000   
1                                  0   1.000000   1.000000   
2                                  0   1.000000   1.000000   
3                                  0   1.000000   1.000000   
4                                  0   1.000000   1.000000   
..                               ...        ...        ...   
25                                 9  19.126303  10.125690   
26                                 6   9.000613   6.750460   
27                                11  10.125690  12.375843   
28                                 9  12.375843  10.125690   
29                                19   5.625383  21.376457   

    same_rs_percentage  same_ra_percentage  both_percentage  
0             5.019802            4.930693         5.000000  
1             4.772277            5.069307         4.940594  
2             5.079208            4.891089         5.079208  
3             5.128713            4.891089         5.148515  
4             4.663366            5.178218         4.821782  
..                 ...                 ...              ...  
25           -3.891089           -3.544554        -3.772277  
26           -3.910891           -4.079208        -4.019802  
27            4.801980            4.742574         4.732673  
28           -3.801980           -3.742574        -3.732673  
29           -4.811881           -4.891089        -4.178218  

[90 rows x 16 columns]

Now that we have done the above for the case of just the first game, we shall now do it just iterating through each of the games in the season, we can then combine them all to see if the proof of concept works

Here we shall do this instead of breaking it up by the game number, we shall do this for each individual team. Thus, for each team we will look at who is the winner, we shall do this for ANA and then generalize to all the others by iterating over the team_list things might also get difficult to code if there are double headers, but we will cross that bridge when we do

In [98]:
team_games = result.loc[result.team == "ANA"]


In [78]:
result

index      Date team opponent  runs_scored  runs_allowed  game_number  \
0        0  20100405  ANA      MIN            6             3            1   
1        1  20100406  ANA      MIN            3             5            2   
2        2  20100407  ANA      MIN            2             4            3   
3        3  20100408  ANA      MIN            1            10            4   
4        4  20100409  ANA      OAK            4            10            5   
..     ...       ...  ...      ...          ...           ...          ...   
157   4855  20100928  WAS      PHI            2             1          158   
158   4856  20100929  WAS      PHI            1             7          159   
159   4857  20101001  WAS      NYN            1             2          160   
160   4858  20101002  WAS      NYN            2             7          161   
161   4859  20101003  WAS      NYN            2             1          162   

     win_loss  previous_cumulative_runs_scored  \
0           1                                0   
1           0                                6   
2           0                                9   
3           0                               11   
4           0                               12   
..        ...                              ...   
157         1                              647   
158         0                              649   
159         0                              650   
160         0                              651   
161         1                              653   

     previous_cumulative_runs_allowed    alpha_rs    alpha_ra  
0                                   0    1.000000    1.000000  
1                                   3    6.750460    3.375230  
2                                   8   10.125690    9.000613  
3                                  12   12.375843   13.500920  
4                                  22   13.500920   24.751687  
..                                ...         ...         ...  
157                               724  727.924607  814.555511  
158                               725  730.174761  815.680588  
159                               732  731.299837  823.556124  
160                               734  732.424914  825.806278  
161                               741  734.675067  833.681814  

[4860 rows x 12 columns]

In [83]:
team_games

index      Date team opponent  runs_scored  runs_allowed  game_number  \
0        0  20100405  ANA      MIN            6             3            1   
1        1  20100406  ANA      MIN            3             5            2   
2        2  20100407  ANA      MIN            2             4            3   
3        3  20100408  ANA      MIN            1            10            4   
4        4  20100409  ANA      OAK            4            10            5   
..     ...       ...  ...      ...          ...           ...          ...   
157    157  20100929  ANA      OAK            2             1          158   
158    158  20100930  ANA      TEX            2             3          159   
159    159  20101001  ANA      TEX            5             4          160   
160    160  20101002  ANA      TEX            2             6          161   
161    161  20101003  ANA      TEX            6             2          162   

     win_loss  previous_cumulative_runs_scored  \
0           1                                0   
1           0                                6   
2           0                                9   
3           0                               11   
4           0                               12   
..        ...                              ...   
157         1                              664   
158         0                              666   
159         1                              668   
160         0                              673   
161         1                              675   

     previous_cumulative_runs_allowed    alpha_rs    alpha_ra  
0                                   0    1.000000    1.000000  
1                                   3    6.750460    3.375230  
2                                   8   10.125690    9.000613  
3                                  12   12.375843   13.500920  
4                                  22   13.500920   24.751687  
..                                ...         ...         ...  
157                               686  747.050911  771.802597  
158                               687  749.301064  772.927674  
159                               690  751.551217  776.302904  
160                               694  757.176601  780.803211  
161                               700  759.426754  787.553671  

[162 rows x 12 columns]

In [99]:
#iterate over all the game numbers
import random
random.seed(10)
team_games.insert(len(team_games.T),"same_rs_percentage",0)
team_games.insert(len(team_games.T),"same_ra_percentage",0)
team_games.insert(len(team_games.T),"both_percentage",0)
for game_number in range(len(team_games)):
    #get the index for where the opponent is for this game
    opponent_index = result.loc[(result.team == team_games.opponent[game_number]) 
                         & (result.opponent == "ANA")
                         & (result.Date == team_games.Date[game_number])
                         & (result.runs_allowed == team_games.runs_scored[game_number])
                        ].values[0][0]
    #gets the alpha values for each team
    home_alpha_rs = team_games.alpha_rs[game_number]
    home_alpha_ra = team_games.alpha_ra[game_number]
    away_alpha_rs = result.reset_index().alpha_rs[opponent_index]
    away_alpha_ra = result.reset_index().alpha_ra[opponent_index]
    
    team1wincount_same_rs = run_simulation_same_rs(home_alpha_rs,away_alpha_rs)
    team1wincount_same_ra = run_simulation_same_ra(home_alpha_ra,away_alpha_ra)
    team1wincount_different = run_simulation_rs_ra (home_alpha_rs, 
                                                    home_alpha_ra, 
                                                    away_alpha_rs,
                                                    away_alpha_ra)
    #print(team1wincount_same_rs)
    team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
    team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
    team_games["both_percentage"][game_number] = team1wincount_different/1001
team_games.insert(len(team_games.T),"same_rs_prediction",(team_games["same_rs_percentage"].values>.5)*1)
team_games.insert(len(team_games.T),"same_ra_prediction",(team_games["same_ra_percentage"].values>.5)*1)
team_games.insert(len(team_games.T),"both_prediction",(team_games["both_percentage"].values>.5)*1)
team_games.insert(len(team_games.T),"same_rs_prediction_correct",(team_games.same_rs_prediction == team_games.win_loss)*1)
team_games.insert(len(team_games.T),"same_ra_prediction_correct",(team_games.same_ra_prediction == team_games.win_loss)*1)
team_games.insert(len(team_games.T),"both_prediction_correct",(team_games.both_prediction == team_games.win_loss)*1)
print("ANA RS Prediction accuracy " + str((team_games.cumsum().same_rs_prediction_correct[161])/162))
print("ANA RA Prediction accuracy " + str((team_games.cumsum().same_ra_prediction_correct[161])/162))
print("ANA Both Prediction accuracy " + str((team_games.cumsum().both_prediction_correct[161])/162))


C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

...

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

ANA RS Prediction accuracy 0.5246913580246914
ANA RA Prediction accuracy 0.4444444444444444
ANA Both Prediction accuracy 0.5370370370370371


C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\391983649.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

In [85]:
team_games

index      Date team opponent  runs_scored  runs_allowed  game_number  \
0        0  20100405  ANA      MIN            6             3            1   
1        1  20100406  ANA      MIN            3             5            2   
2        2  20100407  ANA      MIN            2             4            3   
3        3  20100408  ANA      MIN            1            10            4   
4        4  20100409  ANA      OAK            4            10            5   
..     ...       ...  ...      ...          ...           ...          ...   
157    157  20100929  ANA      OAK            2             1          158   
158    158  20100930  ANA      TEX            2             3          159   
159    159  20101001  ANA      TEX            5             4          160   
160    160  20101002  ANA      TEX            2             6          161   
161    161  20101003  ANA      TEX            6             2          162   

     win_loss  previous_cumulative_runs_scored  \
0           1                                0   
1           0                                6   
2           0                                9   
3           0                               11   
4           0                               12   
..        ...                              ...   
157         1                              664   
158         0                              666   
159         1                              668   
160         0                              673   
161         1                              675   

     previous_cumulative_runs_allowed  ...    alpha_ra  same_rs_percentage  \
0                                   0  ...    1.000000            0.491508   
1                                   3  ...    3.375230            0.514486   
2                                   8  ...    9.000613            0.530470   
3                                  12  ...   13.500920            0.504496   
4                                  22  ...   24.751687            0.467532   
..                                ...  ...         ...                 ...   
157                               686  ...  771.802597            0.521479   
158                               687  ...  772.927674            0.477522   
159                               690  ...  776.302904            0.477522   
160                               694  ...  780.803211            0.483516   
161                               700  ...  787.553671            0.506494   

     same_ra_percentage  both_percentage  same_rs_prediction  \
0              0.495504         0.503497                   0   
1              0.545455         0.497502                   1   
2              0.508492         0.500500                   1   
3              0.498501         0.489510                   1   
4              0.474525         0.529471                   0   
..                  ...              ...                 ...   
157            0.503497         0.489510                   1   
158            0.522478         0.492507                   0   
159            0.492507         0.451548                   0   
160            0.488511         0.473526                   0   
161            0.502498         0.495504                   1   

     same_ra_prediction  both_prediction  same_rs_prediction_correct  \
0                     0                1                           0   
1                     1                0                           0   
2                     1                1                           0   
3                     0                0                           0   
4                     0                1                           1   
..                  ...              ...                         ...   
157                   1                0                           1   
158                   1                0                           1   
159                   0                0                           0   
160                   0                0 

In [100]:
print("ANA RS Prediction accuracy " + str((team_games.cumsum().same_rs_prediction_correct[161])/162))
print("ANA RA Prediction accuracy " + str((team_games.cumsum().same_ra_prediction_correct[161])/162))
print("ANA Both Prediction accuracy " + str((team_games.cumsum().both_prediction_correct[161])/162))


ANA RS Prediction accuracy 0.5246913580246914
ANA RA Prediction accuracy 0.4444444444444444
ANA Both Prediction accuracy 0.5370370370370371


In [91]:
def simulate_for_team(result, team):
    team_games = result.loc[result.team == team]
    #iterate over all the game numbers
    team_games.insert(len(team_games.T),"same_rs_percentage",0)
    team_games.insert(len(team_games.T),"same_ra_percentage",0)
    team_games.insert(len(team_games.T),"both_percentage",0)
    for game_number in range(len(team_games)):
        #get the index for where the opponent is for this game
        opponent_index = result.loc[(result.team == team_games.opponent[game_number]) 
                             & (result.opponent == team)
                             & (result.Date == team_games.Date[game_number])
                             & (result.runs_allowed == team_games.runs_scored[game_number])
                            ].values[0][0]
        #gets the alpha values for each team
        home_alpha_rs = team_games.alpha_rs[game_number]
        home_alpha_ra = team_games.alpha_ra[game_number]
        away_alpha_rs = result.reset_index().alpha_rs[opponent_index]
        away_alpha_ra = result.reset_index().alpha_ra[opponent_index]
        team1wincount_same_rs = run_simulation_same_rs(home_alpha_rs,away_alpha_rs)
        team1wincount_same_ra = run_simulation_same_ra(home_alpha_ra,away_alpha_ra)
        team1wincount_different = run_simulation_rs_ra (home_alpha_rs, 
                                                        home_alpha_ra, 
                                                        away_alpha_rs,
                                                        away_alpha_ra)
        #print(team1wincount_same_rs)
        team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
        team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
        team_games["both_percentage"][game_number] = team1wincount_different/1001
    team_games.insert(len(team_games.T),"same_rs_prediction",(team_games["same_rs_percentage"].values>.5)*1)
    team_games.insert(len(team_games.T),"same_ra_prediction",(team_games["same_ra_percentage"].values>.5)*1)
    team_games.insert(len(team_games.T),"both_prediction",(team_games["both_percentage"].values>.5)*1)
    team_games.insert(len(team_games.T),"same_rs_prediction_correct",(team_games.same_rs_prediction == team_games.win_loss)*1)
    team_games.insert(len(team_games.T),"same_ra_prediction_correct",(team_games.same_ra_prediction == team_games.win_loss)*1)
    team_games.insert(len(team_games.T),"both_prediction_correct",(team_games.both_prediction == team_games.win_loss)*1)
    print(str(team) + "RS Prediction accuracy " + str((team_games.cumsum().same_rs_prediction_correct[161])/162))
    print(str(team) + "RA Prediction accuracy " + str((team_games.cumsum().same_ra_prediction_correct[161])/162))
    print(str(team) + "Both Prediction accuracy " + str((team_games.cumsum().both_prediction_correct[161])/162))
    return team_games

In [41]:
#This will loop through going through each game 
#number of the season
#Make a list for the data frame for each team
frames = []
for team in team_list:
    print(team)
    df = simulate_for_team(result,team) #for each data frame we get the rest of the data we want
    frames.append(df)  #adds the dataframe for that team to the list
final_results = pd.concat(frames)
        

ANA


C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

...

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["both_percentage"][game_number] = team1wincount_different/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guid

C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_rs_percentage"][game_number] = team1wincount_same_rs/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["same_ra_percentage"][game_number] = team1wincount_same_ra/1001
C:\Users\steve\AppData\Local\Temp\ipykernel_13508\402889840.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

WASRS Prediction accuracy 0.5246913580246914
WASRA Prediction accuracy 0.4876543209876543
WASBoth Prediction accuracy 0.5


In [43]:
final_results

index      Date team opponent  runs_scored  runs_allowed  game_number  \
0        0  20100405  ANA      MIN            6             3            1   
1        1  20100406  ANA      MIN            3             5            2   
2        2  20100407  ANA      MIN            2             4            3   
3        3  20100408  ANA      MIN            1            10            4   
4        4  20100409  ANA      OAK            4            10            5   
..     ...       ...  ...      ...          ...           ...          ...   
157   4855  20100928  WAS      PHI            2             1          158   
158   4856  20100929  WAS      PHI            1             7          159   
159   4857  20101001  WAS      NYN            1             2          160   
160   4858  20101002  WAS      NYN            2             7          161   
161   4859  20101003  WAS      NYN            2             1          162   

     win_loss  previous_cumulative_runs_scored  \
0           1                                0   
1           0                                6   
2           0                                9   
3           0                               11   
4           0                               12   
..        ...                              ...   
157         1                              647   
158         0                              649   
159         0                              650   
160         0                              651   
161         1                              653   

     previous_cumulative_runs_allowed  ...    alpha_ra  same_rs_percentage  \
0                                   0  ...    1.000000            0.525475   
1                                   3  ...    3.375230            0.532468   
2                                   8  ...    9.000613            0.483516   
3                                  12  ...   13.500920            0.490509   
4                                  22  ...   24.751687            0.489510   
..                                ...  ...         ...                 ...   
157                               724  ...  814.555511            0.492507   
158                               725  ...  815.680588            0.493506   
159                               732  ...  823.556124            0.478521   
160                               734  ...  825.806278            0.509491   
161                               741  ...  833.681814            0.495504   

     same_ra_percentage  both_percentage  same_rs_prediction  \
0              0.499500         0.501499                   1   
1              0.542458         0.505495                   1   
2              0.483516         0.518482                   0   
3              0.507493         0.490509                   0   
4              0.471528         0.501499                   0   
..                  ...              ...                 ...   
157            0.482517         0.489510                   0   
158            0.491508         0.476523                   0   
159            0.476523         0.510490                   0   
160            0.478521         0.489510                   1   
161            0.489510         0.511489                   0   

     same_ra_prediction  both_prediction  same_rs_prediction_correct  \
0                     0                1                           1   
1                     1                1                           0   
2                     0                1                           1   
3                     1                0                           1   
4                     0                1                           1   
..                  ...              ...                         ...   
157                   0                0                           0   
158                   0                0                           1   
159                   0                1                           1   
160                   0                0 

In [49]:
final_results.reset_index().cumsum().both_prediction_correct[4859]/4860

0.5111111111111111

In [50]:
print("RS Prediction accuracy " + str((final_results.reset_index().cumsum().same_rs_prediction_correct[4859])/4860))
print("RA Prediction accuracy " + str((final_results.reset_index().cumsum().same_ra_prediction_correct[4859])/4860))
print("Both Prediction accuracy " + str((final_results.reset_index().cumsum().both_prediction_correct[4859])/4860))

RS Prediction accuracy 0.5139917695473251
RA Prediction accuracy 0.5273662551440329
Both Prediction accuracy 0.5111111111111111


Note: for the entire season it seems as though this model is only marginally better than flipping a coin, but at the beginning of the season we pretty much were just flipping a coin, so we might think about if we just take all the games of the season starting after game 50 (we can change this) since this metric is used part way through the season

In [55]:
LaterSeasondf = final_results.loc[final_results.game_number >=75]

In [58]:
LaterSeasondf

index      Date team opponent  runs_scored  runs_allowed  game_number  \
74      74  20100624  ANA      LAN            6            10           75   
75      75  20100625  ANA      COL            3             4           76   
76      76  20100626  ANA      COL            4             2           77   
77      77  20100627  ANA      COL           10             3           78   
78      78  20100629  ANA      TEX            6             5           79   
..     ...       ...  ...      ...          ...           ...          ...   
157   4855  20100928  WAS      PHI            2             1          158   
158   4856  20100929  WAS      PHI            1             7          159   
159   4857  20101001  WAS      NYN            1             2          160   
160   4858  20101002  WAS      NYN            2             7          161   
161   4859  20101003  WAS      NYN            2             1          162   

     win_loss  previous_cumulative_runs_scored  \
74          0                              349   
75          0                              355   
76          1                              358   
77          1                              362   
78          1                              372   
..        ...                              ...   
157         1                              647   
158         0                              649   
159         0                              650   
160         0                              651   
161         1                              653   

     previous_cumulative_runs_allowed  ...    alpha_ra  same_rs_percentage  \
74                                355  ...  399.402219            0.514486   
75                                365  ...  410.652985            0.505495   
76                                369  ...  415.153292            0.530470   
77                                371  ...  417.403446            0.499500   
78                                374  ...  420.778676            0.499500   
..                                ...  ...         ...                 ...   
157                               724  ...  814.555511            0.492507   
158                               725  ...  815.680588            0.493506   
159                               732  ...  823.556124            0.478521   
160                               734  ...  825.806278            0.509491   
161                               741  ...  833.681814            0.495504   

     same_ra_percentage  both_percentage  same_rs_prediction  \
74             0.500500         0.507493                   1   
75             0.461538         0.497502                   1   
76             0.492507         0.514486                   1   
77             0.485514         0.547453                   0   
78             0.479520         0.479520                   0   
..                  ...              ...                 ...   
157            0.482517         0.489510                   0   
158            0.491508         0.476523                   0   
159            0.476523         0.510490                   0   
160            0.478521         0.489510                   1   
161            0.489510         0.511489                   0   

     same_ra_prediction  both_prediction  same_rs_prediction_correct  \
74                    1                1                           0   
75                    0                0                           0   
76                    0                1                           1   
77                    0                1                           0   
78                    0                0                           0   
..                  ...              ...                         ...   
157                   0                0                           0   
158                   0                0                           1   
159                   0                1                           1   
160                   0                0 

In [60]:
print("Prediction after game number " + number)
print("RS Prediction accuracy " + str((LaterSeasondf.reset_index().cumsum().same_rs_prediction_correct[len(LaterSeasondf)-1])/len(LaterSeasondf)))
print("RA Prediction accuracy " + str((LaterSeasondf.reset_index().cumsum().same_ra_prediction_correct[len(LaterSeasondf)-1])/len(LaterSeasondf)))
print("Both Prediction accuracy " + str((LaterSeasondf.reset_index().cumsum().both_prediction_correct[len(LaterSeasondf)-1])/len(LaterSeasondf)))

RS Prediction accuracy 0.5261363636363636
RA Prediction accuracy 0.5265151515151515
Both Prediction accuracy 0.5037878787878788


In [62]:
for number in range(75,100):
    LaterSeasondf = final_results.loc[final_results.game_number >=number]
    print("Prediction after game number " + str(number))
    print("RS Prediction accuracy " + str((LaterSeasondf.reset_index().cumsum().same_rs_prediction_correct[len(LaterSeasondf)-1])/len(LaterSeasondf)))
    print("RA Prediction accuracy " + str((LaterSeasondf.reset_index().cumsum().same_ra_prediction_correct[len(LaterSeasondf)-1])/len(LaterSeasondf)))
    print("Both Prediction accuracy " + str((LaterSeasondf.reset_index().cumsum().both_prediction_correct[len(LaterSeasondf)-1])/len(LaterSeasondf)))

Prediction after game number 75
RS Prediction accuracy 0.5261363636363636
RA Prediction accuracy 0.5265151515151515
Both Prediction accuracy 0.5037878787878788
Prediction after game number 76
RS Prediction accuracy 0.5264367816091954
RA Prediction accuracy 0.5252873563218391
Both Prediction accuracy 0.5019157088122606
Prediction after game number 77
RS Prediction accuracy 0.5290697674418605
RA Prediction accuracy 0.525968992248062
Both Prediction accuracy 0.5015503875968992
Prediction after game number 78
RS Prediction accuracy 0.5294117647058824
RA Prediction accuracy 0.5266666666666666
Both Prediction accuracy 0.4992156862745098
Prediction after game number 79
RS Prediction accuracy 0.528968253968254
RA Prediction accuracy 0.5285714285714286
Both Prediction accuracy 0.4992063492063492
Prediction after game number 80
RS Prediction accuracy 0.5289156626506024
RA Prediction accuracy 0.5301204819277109
Both Prediction accuracy 0.4971887550200803
Prediction after game number 81
RS Predict